In [1]:
import pandas as pd
import plotly.express as px
import json
from parametric_umap import ParametricUMAP

# Common Metadata

In [2]:
tcga_oncontree = pd.read_csv('/home/fcarli/francisCelligner/tcga_oncotree_data_correct.csv')
ccle_oncontree = pd.read_csv('/home/fcarli/CellHit/data/metadata/Model.csv')

In [3]:
with open('/home/fcarli/francisCelligner/tissueMap.json','r') as f:
    mainTypeMap = json.load(f)

# Graphical check

In [4]:
df = pd.read_feather('/home/fcarli/WebCellHit/data/transcriptomics/celligner_CCLE_TCGA_optimized_revised.feather')

In [7]:
tcga_oncontree['tissue'] = tcga_oncontree['oncotree_code'].map(mainTypeMap)
ccle_oncontree['tissue'] = ccle_oncontree['OncotreeCode'].map(mainTypeMap)

#map tissue
tcga_mapper = dict(zip(tcga_oncontree['sample_id'],tcga_oncontree['tissue']))
ccle_mapper = dict(zip(ccle_oncontree['ModelID'],ccle_oncontree['tissue']))

#map oncotree code
tcga_oncotree_mapper = dict(zip(tcga_oncontree['sample_id'],tcga_oncontree['oncotree_code']))
ccle_oncotree_mapper = dict(zip(ccle_oncontree['ModelID'],ccle_oncontree['OncotreeCode']))


In [8]:
tcga = df[df['Source']=='TCGA']
ccle = df[df['Source']=='CCLE']

In [9]:
#get all columns except the first two
genes = tcga.columns[2:]
genes

Index(['GPR18', 'GK2', 'NXF5', 'AHCYL1', 'TMOD1', 'MEGF6', 'P2RY14', 'RCC2',
       'XRN1', 'SIGMAR1',
       ...
       'BMP4', 'RBMY1J', 'FXYD5', 'STK38', 'LSM8', 'ISCA2', 'IFNL2', 'INS',
       'DUX4', 'MKRN3'],
      dtype='object', length=18174)

In [10]:
tcga['tissue'] = tcga['index'].map(tcga_mapper)
ccle['tissue'] = ccle['index'].map(ccle_mapper)
tcga['oncotree_code'] = tcga['index'].map(tcga_oncotree_mapper)
ccle['oncotree_code'] = ccle['index'].map(ccle_oncotree_mapper)
tcga.dropna(inplace=True,subset=['tissue'])   
ccle.dropna(inplace=True,subset=['tissue'])
tcga.dropna(inplace=True,subset=['oncotree_code'])
ccle.dropna(inplace=True,subset=['oncotree_code'])


/tmp/ipykernel_80008/912924964.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tcga['tissue'] = tcga['index'].map(tcga_mapper)
/tmp/ipykernel_80008/912924964.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ccle['tissue'] = ccle['index'].map(ccle_mapper)
/tmp/ipykernel_80008/912924964.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/

/tmp/ipykernel_80008/912924964.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tcga.dropna(inplace=True,subset=['tissue'])
/tmp/ipykernel_80008/912924964.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ccle.dropna(inplace=True,subset=['tissue'])
/tmp/ipykernel_80008/912924964.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tcga.dropna(inplace=True,subset=['oncotree_code'])
/tmp/ipykernel_80008/912924964.py:8: SettingWithCop

In [12]:
overall_expression = pd.concat([tcga,ccle])[genes]
overall_expression['tissue'] = list(tcga['tissue'])+list(ccle['tissue'])
overall_expression['oncotree_code'] = list(tcga['oncotree_code'])+list(ccle['oncotree_code'])
overall_expression['Source'] = list(tcga['Source'])+list(ccle['Source'])
overall_expression['index'] = list(tcga['index'])+list(ccle['index'])

In [11]:
umap = ParametricUMAP(n_components=2,
                                n_epochs=3,
                                n_neighbors=15,
                                batch_size=64,
                                correlation_weight=0.05,
                                device='cuda:3')

umap_embedding = umap.fit_transform(overall_expression[genes].values)
#umap.save('/home/fcarli/WebCellHit/webserver_data/local_data/umap.trc')


Sampling negative edges...


Completed processes:   0%|          | 0/6 [00:00<?, ?it/s]

Training...


Epochs:   0%|          | 0/2 [00:00<?, ?it/s]

Epoch 1:   0%|          | 0/26053 [00:00<?, ?it/s]

Epoch 1/2, Loss: 0.0981


Epoch 2:   0%|          | 0/26053 [00:00<?, ?it/s]

Epoch 2/2, Loss: 0.0855


In [15]:
#load the uma
umap = ParametricUMAP.load('/home/fcarli/WebCellHit/webserver_data/local_data/umap.trc')
umap_embedding = umap.transform(overall_expression[genes].values)

/scratch/fcarli/envs/francisCelligner/lib/python3.11/site-packages/parametric_umap/core.py:279: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  save_dict = torch.load(path, ma

In [17]:
# Perform t-SNE
# Create a DataFrame with t-SNE results
tsne_df = pd.DataFrame(umap_embedding, columns=['TSNE1', 'TSNE2'])
tsne_df['tissue'] = overall_expression['tissue'].values
tsne_df['oncotree_code'] = overall_expression['oncotree_code'].values
tsne_df['Source'] = overall_expression['Source'].values
tsne_df['index'] = overall_expression['index'].values

# Optionally, define a symbol map if you want specific markers for each Source
# For example:
symbol_map = {
    'TCGA': 'cross',
    'CCLE': 'circle',
    #'OtherSource': 'diamond'
}

# Create scatter plot with Plotly, adding symbols based on 'Source'
fig = px.scatter(
    tsne_df,
    x='TSNE1',
    y='TSNE2',
    color='tissue',
    symbol='Source',  # Assign different markers based on 'Source'
    symbol_map=symbol_map,  # Uncomment if you defined a symbol_map
    title='t-SNE of Combined TCGA and CCLE Gene Expression Data',
    hover_data=['tissue', 'oncotree_code', 'Source', 'index']  # Optionally include in hover
)

# Customize the layout
fig.update_layout(
    legend_title_text='Oncotree Code and Source',  # Adjusted for multiple legends
    #legend=dict(
    #    # You can customize legend layout here if needed
    #),
    width=1000,
    height=800,
)

# Optionally, customize the marker symbols and sizes further
fig.update_traces(marker=dict(size=6, line=dict(width=0.2, color='DarkSlateGrey')))

# Show the plot
fig.show()


In [19]:
tsne_df.to_csv('/home/fcarli/WebCellHit/webserver_data/local_data/overall_tsne_df.csv')